# 5D Kerr-AdS spacetime: general solution with 2 angular momenta

This notebook demonstrates a few capabilities of SageMath in computations regarding the 5-dimensional Kerr-AdS spacetime. The corresponding tools have been developed within the  [SageManifolds](https://sagemanifolds.obspm.fr) project (version 1.3, as included in SageMath 8.3).

Click [here](https://raw.githubusercontent.com/sagemanifolds/SageManifolds/master/Worksheets/v1.3/SM_Kerr-AdS_5D.ipynb) to download the notebook file (ipynb format). To run it, you must start SageMath within the Jupyter notebook, via the command `sage -n jupyter`

*NB:* a version of SageMath at least equal to 8.2 is required to run this notebook:

In [1]:
version()

'SageMath version 8.3, Release Date: 2018-08-03'

First we set up the notebook to display mathematical objects using LaTeX rendering:

In [2]:
%display latex

Since some computations are quite long, we ask for running them in parallel on 8 cores:

In [3]:
Parallelism().set(nproc=8)

## Spacetime manifold

We declare the Kerr-AdS spacetime as a 5-dimensional Lorentzian manifold:

In [4]:
M = Manifold(5, 'M', latex_name=r'\mathcal{M}', structure='Lorentzian')
print(M)

5-dimensional Lorentzian manifold M


Let us define **Boyer-Lindquist-type coordinates (rational polynomial version)** on $\mathcal{M}$, via the method `chart()`, the argument of which is a string expressing the coordinates names, their ranges (the default is $(-\infty,+\infty)$) and their LaTeX symbols:

In [5]:
BL.<t,r,mu,ph,ps> = M.chart(r't r:(0,+oo) mu:(-1,1):\mu ph:(0,2*pi):\phi ps:(0,2*pi):\psi')
BL

Chart (M, (t, r, mu, ph, ps))

Note that $\mu$ is related to the standard Boyer-Lindquist coordinate $\theta$ by
$$ \mu = \cos\theta$$

## Metric tensor

The 4 parameters $m$, $a$, $b$ and $\ell$ of the Kerr-AdS spacetime are declared as symbolic variables, $a$ and $b$ being the two angular momentum parameters and $\ell$ being related to the cosmological constant by $\Lambda = - 6 \ell^2$:

In [6]:
var('m a b', domain='real')

(m, a, b)

In [7]:
var('l', domain='real', latex_name=r'\ell')

l

In [8]:
# Particular cases
# a = 0
# m = 0
# b = a

Some auxiliary functions:

In [9]:
sig = (1+r^2*l^2)/r^2
Delta = (r^2+a^2)*(r^2+b^2)*sig - 2*m
sinth2 = 1-mu^2
Delta_th = 1 - a^2*l^2*mu^2 - b^2*l^2*sinth2
rho2 = r^2 + a^2*mu^2 + b^2*sinth2
Xi_a = 1 - a^2*l^2
Xi_b = 1 - b^2*l^2

The metric is set by its components in the coordinate frame associated with the Boyer-Lindquist-type coordinates, which is the current manifold's default frame. These components are given by 
Eq. (5.22) of the article [S.W. Hawking, C.J. Hunter & M.M. Taylor-Robinson, Phys. Rev. D **59**, 064005 (1999)](https://doi.org/10.1103/PhysRevD.59.064005):

In [10]:
g = M.metric()
tmp = 1/rho2*( -Delta + Delta_th*(a^2*sinth2 + b^2*mu^2) + a^2*b^2*sig )
g[0,0] = tmp.simplify_full()
tmp = a*sinth2/(rho2*Xi_a)*( Delta - (r^2+a^2)*(Delta_th + b^2*sig) )
g[0,3] = tmp.simplify_full()
tmp = b*mu^2/(rho2*Xi_b)*( Delta - (r^2+b^2)*(Delta_th + a^2*sig) )
g[0,4] = tmp.simplify_full()
g[1,1] = (rho2/Delta).simplify_full()
g[2,2] = (rho2/Delta_th/(1-mu^2)).simplify_full()
tmp = sinth2/(rho2*Xi_a^2)*( - Delta*a^2*sinth2 + (r^2+a^2)^2*(Delta_th + sig*b^2*sinth2) ) 
g[3,3] = tmp.simplify_full()
tmp = a*b*sinth2*mu^2/(rho2*Xi_a*Xi_b)*( - Delta + sig*(r^2+a^2)*(r^2+b^2) )
g[3,4] = tmp.simplify_full()
tmp = mu^2/(rho2*Xi_b^2)*( - Delta*b^2*mu^2 + (r^2+b^2)^2*(Delta_th + sig*a^2*mu^2) )
g[4,4] = tmp.simplify_full()

In [11]:
g.display_comp(only_nonredundant=True)

g_t,t = ((a^4 - 2*a^2*b^2 + b^4)*l^2*mu^4 - a^2*b^2*l^2 - l^2*r^4 - ((a^4 - 2*a^2*b^2 + b^4)*l^2 + a^2 - b^2)*mu^2 - ((a^2 + b^2)*l^2 + 1)*r^2 - b^2 + 2*m)/((a^2 - b^2)*mu^2 + b^2 + r^2) 
g_t,ph = -(a^3*b^2*l^2 - (a^5 - a^3*b^2)*l^2*mu^4 - (a*l^2*mu^2 - a*l^2)*r^4 + ((a^5 - 2*a^3*b^2)*l^2 + 2*a*m)*mu^2 - (2*a*b^2*l^2*mu^2 + (a^3 - a*b^2)*l^2*mu^4 - (a^3 + a*b^2)*l^2)*r^2 - 2*a*m)/(a^2*b^2*l^2 + ((a^4 - a^2*b^2)*l^2 - a^2 + b^2)*mu^2 + (a^2*l^2 - 1)*r^2 - b^2) 
g_t,ps = -(b*l^2*mu^2*r^4 + (a^2*b^3 - b^5)*l^2*mu^4 + (b^5*l^2 - 2*b*m)*mu^2 + (2*b^3*l^2*mu^2 + (a^2*b - b^3)*l^2*mu^4)*r^2)/(b^4*l^2 + ((a^2*b^2 - b^4)*l^2 - a^2 + b^2)*mu^2 + (b^2*l^2 - 1)*r^2 - b^2) 
g_r,r = (r^4 + ((a^2 - b^2)*mu^2 + b^2)*r^2)/(l^2*r^6 + ((a^2 + b^2)*l^2 + 1)*r^4 + a^2*b^2 + (a^2*b^2*l^2 + a^2 + b^2 - 2*m)*r^2) 
g_mu,mu = ((a^2 - b^2)*mu^2 + b^2 + r^2)/((a^2 - b^2)*l^2*mu^4 - b^2*l^2 - ((a^2 - 2*b^2)*l^2 + 1)*mu^2 + 1) 
g_ph,ph = -(a^4*b^2*l^2 + (a^4 - a^2*b^2 - (a^6 - a^4*b^2)*l^2 - 2*a^2*m)*mu^4 + (a^2*l^2 - (a^2*l^2 - 1)*mu^2 - 1)*r^4 - a^2*b^2 - 2*a^2*m - (a^4 - 2*a^2*b^2 - (a^6 - 2*a^4*b^2)*l^2 - 4*a^2*m)*mu^2 - (((a^4 - a^2*b^2)*l^2 - a^2 + b^2)*mu^4 - (a^4 + a^2*b^2)*l^2 + 2*(a^2*b^2*l^2 - b^2)*mu^2 + a^2 + b^2)*r^2)/(a^4*b^2*l^4 - 2*a^2*b^2*l^2 + ((a^6 - a^4*b^2)*l^4 - 2*(a^4 - a^2*b^2)*l^2 + a^2 - b^2)*mu^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + b^2) 
g_ph,ps = -2*(a*b*m*mu^4 - a*b*m*mu^2)/(a^2*b^4*l^4 - (a^2*b^2 + b^4)*l^2 + ((a^4*b^2 - a^2*b^4)*l^4 - (a^4 - b^4)*l^2 + a^2 - b^2)*mu^2 + (a^2*b^2*l^4 - (a^2 + b^2)*l^2 + 1)*r^2 + b^2) 
g_ps,ps = -((b^2*l^2 - 1)*mu^2*r^4 - (a^2*b^2 - b^4 - (a^2*b^4 - b^6)*l^2 + 2*b^2*m)*mu^4 + (b^6*l^2 - b^4)*mu^2 + (((a^2*b^2 - b^4)*l^2 - a^2 + b^2)*mu^4 + 2*(b^4*l^2 - b^2)*mu^2)*r^2)/(b^6*l^4 - 2*b^4*l^2 + ((a^2*b^4 - b^6)*l^4 - 2*(a^2*b^2 - b^4)*l^2 + a^2 - b^2)*mu^2 + (b^4*l^4 - 2*b^2*l^2 + 1)*r^2 + b^2)

## Einstein equation

The Ricci tensor of $g$ is

In [12]:
Ric = g.ricci()
print(Ric)

Field of symmetric bilinear forms Ric(g) on the 5-dimensional Lorentzian manifold M


In [13]:
Ric.display_comp(only_nonredundant=True)

Ric(g)_t,t = -4*((a^4 - 2*a^2*b^2 + b^4)*l^4*mu^4 - a^2*b^2*l^4 - l^4*r^4 - b^2*l^2 + 2*l^2*m - ((a^4 - 2*a^2*b^2 + b^4)*l^4 + (a^2 - b^2)*l^2)*mu^2 - ((a^2 + b^2)*l^4 + l^2)*r^2)/((a^2 - b^2)*mu^2 + b^2 + r^2) 
Ric(g)_t,ph = 4*(a^3*b^2*l^4 - (a^5 - a^3*b^2)*l^4*mu^4 - (a*l^4*mu^2 - a*l^4)*r^4 - 2*a*l^2*m + ((a^5 - 2*a^3*b^2)*l^4 + 2*a*l^2*m)*mu^2 - (2*a*b^2*l^4*mu^2 + (a^3 - a*b^2)*l^4*mu^4 - (a^3 + a*b^2)*l^4)*r^2)/(a^2*b^2*l^2 + ((a^4 - a^2*b^2)*l^2 - a^2 + b^2)*mu^2 + (a^2*l^2 - 1)*r^2 - b^2) 
Ric(g)_t,ps = 4*(b*l^4*mu^2*r^4 + (a^2*b^3 - b^5)*l^4*mu^4 + (b^5*l^4 - 2*b*l^2*m)*mu^2 + (2*b^3*l^4*mu^2 + (a^2*b - b^3)*l^4*mu^4)*r^2)/(b^4*l^2 + ((a^2*b^2 - b^4)*l^2 - a^2 + b^2)*mu^2 + (b^2*l^2 - 1)*r^2 - b^2) 
Ric(g)_r,r = -4*(l^2*r^4 + ((a^2 - b^2)*l^2*mu^2 + b^2*l^2)*r^2)/(l^2*r^6 + ((a^2 + b^2)*l^2 + 1)*r^4 + a^2*b^2 + (a^2*b^2*l^2 + a^2 + b^2 - 2*m)*r^2) 
Ric(g)_mu,mu = -4*((a^2 - b^2)*l^2*mu^2 + b^2*l^2 + l^2*r^2)/((a^2 - b^2)*l^2*mu^4 - b^2*l^2 - ((a^2 - 2*b^2)*l^2 + 1)*mu^2 + 1) 
Ric(g)_ph,ph = 4*(a^4*b^2*l^4 - a^2*b^2*l^2 - 2*a^2*l^2*m - ((a^6 - a^4*b^2)*l^4 + 2*a^2*l^2*m - (a^4 - a^2*b^2)*l^2)*mu^4 + (a^2*l^4 - (a^2*l^4 - l^2)*mu^2 - l^2)*r^4 + ((a^6 - 2*a^4*b^2)*l^4 + 4*a^2*l^2*m - (a^4 - 2*a^2*b^2)*l^2)*mu^2 + ((a^4 + a^2*b^2)*l^4 - ((a^4 - a^2*b^2)*l^4 - (a^2 - b^2)*l^2)*mu^4 - (a^2 + b^2)*l^2 - 2*(a^2*b^2*l^4 - b^2*l^2)*mu^2)*r^2)/(a^4*b^2*l^4 - 2*a^2*b^2*l^2 + ((a^6 - a^4*b^2)*l^4 - 2*(a^4 - a^2*b^2)*l^2 + a^2 - b^2)*mu^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + b^2) 
Ric(g)_ph,ps = 8*(a*b*l^2*m*mu^4 - a*b*l^2*m*mu^2)/(a^2*b^4*l^4 - (a^2*b^2 + b^4)*l^2 + ((a^4*b^2 - a^2*b^4)*l^4 - (a^4 - b^4)*l^2 + a^2 - b^2)*mu^2 + (a^2*b^2*l^4 - (a^2 + b^2)*l^2 + 1)*r^2 + b^2) 
Ric(g)_ps,ps = 4*((b^2*l^4 - l^2)*mu^2*r^4 + ((a^2*b^4 - b^6)*l^4 - 2*b^2*l^2*m - (a^2*b^2 - b^4)*l^2)*mu^4 + (b^6*l^4 - b^4*l^2)*mu^2 + (((a^2*b^2 - b^4)*l^4 - (a^2 - b^2)*l^2)*mu^4 + 2*(b^4*l^4 - b^2*l^2)*mu^2)*r^2)/(b^6*l^4 - 2*b^4*l^2 + ((a^2*b^4 - b^6)*l^4 - 2*(a^2*b^2 - b^4)*l^2 + a^2 - b^2)*mu^2 + (b^4*l^4 - 2*b^2*l^2 + 1)*r^2 + b^2)

Let us check that $g$ is a solution of the vacuum Einstein equation with the cosmological constant $\Lambda = - 6 \ell^2$:

In [14]:
Lambda = -6*l^2
Ric == 2/3*Lambda*g

True